In [1]:
import numpy as np
import pandas as pd
import copy
import matplotlib.pyplot as plt
import requests
import math
import requests
from operator import itemgetter
from datetime import datetime
import time

# High Dividend Yield Stock Screening Criteria
# Market Capitalization > 2 B
# Dividend Yield > 3% < 10%######>1.5%
# Dividend 1 Year Change % > 2%
# Dividend 3 Year Average % > 2%
# Payout Ratio > 30 and < 60

# 安全股息筛选标准
# 市值 > 20 亿美元
# 股息收益率 > 1.5%
# 股息 1 年变化 % > 0%
# 股息 3 年平均百分比 > 0%
# 股息 5 年平均百分比 > 0%
# 主要交易所（非场外交易）的股票
# 支付比率 > 30 和 < 50
# 5 年平均销售额增长 > 4.5%


def high_div(symbols):

    api_key1 = '8a1cf9d14d53126b05c8a7636fe3d006'
    stocks = pd.DataFrame(columns = ['mktCap','price','symbol','volAvg','lastDiv'])
    #ticker = 'FAST'
    for ticker in symbols:
        try:
            bs =requests.get(f'https://financialmodelingprep.com/api/v3/profile/{ticker}?apikey={api_key1}').json()[0]
            stocks = stocks.append({'mktCap':bs['mktCap'],'price':bs['price'], 'symbol':bs['symbol'], 'volAvg':bs['volAvg'],'lastDiv':bs['lastDiv']}, ignore_index=True)
            stocks['dividend_yield'] = stocks['lastDiv']/stocks['price']
        except:
            pass
    stocks =stocks.set_index('symbol')
        
    
    api_key1 = '8a1cf9d14d53126b05c8a7636fe3d006'
    stocks1 = pd.DataFrame(columns = ['dividendYielPercentageTTM','payoutRatioTTM','symbol'])
    for ticker in symbols:
        try:
            bs =requests.get(f'https://financialmodelingprep.com/api/v3/ratios-ttm/{ticker}?apikey={api_key1}').json()[0]
            stocks1 = stocks1.append({'dividendYielPercentageTTM':bs['dividendYielPercentageTTM'],'payoutRatioTTM':bs['payoutRatioTTM'], 'symbol':ticker}, ignore_index=True)
        except:
            pass
    stocks1 =stocks1.set_index('symbol')        

    ############DIVIDEND ARE BASED ON YEARLY###############
    stocks2 = pd.DataFrame(columns = [ "fiveYDividendperShareGrowthPerShare", "threeYDividendperShareGrowthPerShare"])
    
    for ticker in symbols:
        try:
            bs =requests.get(f'https://financialmodelingprep.com/api/v3/financial-growth/{ticker}?apikey={api_key1}').json()[0]
            stocks2 = stocks2.append({"fiveYDividendperShareGrowthPerShare":bs["fiveYDividendperShareGrowthPerShare"],"threeYDividendperShareGrowthPerShare":bs["threeYDividendperShareGrowthPerShare"], 'symbol':ticker}, ignore_index=True)
    
        except:
            pass
    stocks2 =stocks2.set_index('symbol')             
    
    stocks1 = stocks1.sort_index()
    stocks2=stocks2.sort_index()
    stocks=stocks.sort_index()
    all_data = pd.concat([stocks, stocks2,stocks1], axis=1, join="inner")
    #  all_data 
    # data=stocks.merge(stocks1, left_index=True, right_index=True)
    # all_data = data.merge(stocks2,left_index=True, right_index=True)
    
   #all_data =all_data.dropna()

    div = pd.DataFrame()
    for ticker in symbols:
        try:
            bs =requests.get(f'https://financialmodelingprep.com/api/v3/historical-price-full/stock_dividend/{ticker}?apikey={api_key1}').json()['historical']
            dividend=pd.DataFrame(columns = ['date','dividend'])
            for i in range(len(bs)):
                dividend= dividend.append({'date':bs[i]['date'], 'dividend':bs[i]['dividend']}, ignore_index = True)
                
            dividend_data = pd.DataFrame(columns = ['date','dividend'])
            for i in range(1,len(dividend)):
                dividend_data =  dividend_data.append({'date':bs[i]['date'], 'dividend':bs[i]['dividend']}, ignore_index = True)
                if i >21:
                    break 
            
            
            div_data = pd.DataFrame(columns = ['date','dividendAvg'])
            for i in range(6):
                div_data=  div_data.append({'date': dividend_data['date'][ 4*i], 'dividendAvg':dividend_data['dividend'][ 4*i]},ignore_index = True)
            
            div_data ['dividendAvg'] =div_data['dividendAvg']*4
            avg_div3y = div_data.loc[1:3,'dividendAvg'].mean()
            avg_div5y =div_data.loc[1:5,'dividendAvg'].mean()
            one_yearchange = (div_data.loc[0,'dividendAvg']-div_data.loc[1,'dividendAvg'])/div_data.loc[1,'dividendAvg']
            dataa =pd.DataFrame(columns = ['symbol', 'avg_div3y','avgdiv5y', 'one_yearchange'])
            dataa = dataa.append({'symbol':ticker, 'avg_div3y':avg_div3y ,'avgdiv5y':avg_div5y,'one_yearchange':one_yearchange}, ignore_index = True)
            div =pd.concat([div,dataa], axis =0)
            
        except:
            pass
    div= div.set_index('symbol')
    #div =div.dropna()
    div = div.sort_index()
    
    all_data1 = pd.concat([ all_data ,div], axis=1, join="inner")
  #  all_data1 = all_data.merge(div,left_index=True, right_index=True)
    all_data1= all_data1.dropna()
        
    all_data1 = all_data1[all_data1['mktCap'] >2000000000]
    all_data1 =  all_data1[all_data1['dividend_yield'] >0.015]
    all_data1 =  all_data1[all_data1['one_yearchange'] >0.02]
    all_data1 =  all_data1[all_data1["avg_div3y"]>0]
    all_data1 =  all_data1[all_data1[ "avgdiv5y"]>0]
    all_data1 = all_data1[all_data1['payoutRatioTTM'] > 0.3] 
    all_data1 = all_data1[ all_data1['payoutRatioTTM'] <0.8]
    return all_data1

In [2]:
d =pd.read_csv(r'C:\Users\jizha\Desktop\seabridge_datapool1\stock_lists.csv' ) 
symbols = list(d['0']) 


In [5]:
n =3
high_dividend =pd.DataFrame()
groups = np.array_split(symbols, n)
import time
for group in groups:
    for ticker in group:
        hig_dividend = high_div(ticker)
    high_dividend = pd.concat([high_dividend,hig_dividend],axis =0)
    time.sleep(60)

InvalidIndexError: Reindexing only valid with uniquely valued Index objects

In [3]:
n = 3# number of groups
groups = np.array_split(symbols, n)
group1 = groups[0].tolist()
group2 = groups[1].tolist()
group3 = groups[2].tolist()
#group4 = groups[3].tolist()
#group5 = groups[4].tolist()


In [4]:
data1 =high_div(group1)

In [7]:
data1

mktCap   price    volAvg  lastDiv  dividend_yield  \
symbol                                                            
ADI      60321656832  163.55   3212253   2.6200        0.016020   
ADM      32410302464   58.01   2604460   1.4600        0.025168   
ADP      87690756096  206.08   1574004   3.7000        0.017954   
AEE      21310564352   83.39   1324761   2.1100        0.025303   
AEP      43011584000   85.98   2770652   2.9200        0.033961   
AIZ       9389034496  155.02    343871   2.6100        0.016837   
AJG      29502201856  143.05   1190671   1.8600        0.013002   
AMGN    142328512512  247.72   2611580   6.7200        0.027127   
AOS      11172550656   69.63   1051630   1.2800        0.018383   
APD      64245243904  290.29    854552   5.6800        0.019567   
ARE      29049831424  196.94    856279   4.3600        0.022139   
ATO      13006767104   99.45    759430   2.4500        0.024635   
AVY      16788306944  202.25    526330   2.5000        0.012361   
AWK      30354319360  167.27    732879   2.2525        0.013466   
BAX      40801411072   81.14   2579457   1.0150        0.012509   
BDX      73018580992  251.08   1400515   3.2800        0.013064   
BEN      14776664064   29.30   2794096   1.1100        0.037884   
BLK     132340228096  868.95    568319  15.5200        0.017861   
BR       20030574592  172.49    477080   2.3000        0.013334   
BX       80188866560  111.30   4141934   2.6900        0.024169   
CAG      16438184960   34.25   3343665   1.3510        0.039445   
CBOE     12823656448  120.20    550853   1.6800        0.013977   
CL       70452297728   83.28   3961273   1.7800        0.021374   
CLX      22980214784  184.77   1373888   5.6000        0.030308   
CMCSA   268122783744   58.36  15820358   0.9600        0.016450   
CMI      34714443776  237.44    984080   5.3610        0.022578   
CMS      17969678336   62.08   2499557   2.1210        0.034166   
CPB      13506982912   44.57   2545341   1.4600        0.032757   
CSCO    232750268416   55.23  18222023   1.4600        0.026435   
CSX      73970147328   32.81  11513803   0.4533        0.013816   
EMN      15002457088  110.05    716368   2.7300        0.024807   
ES       29613637632   86.22   1657903   2.3415        0.027157   
ETR      20615806976  102.74   1008465   3.7800        0.036792   
EVRG     14920762368   65.08   1202790   2.1100        0.032422   

        fiveYDividendperShareGrowthPerShare  \
symbol                                        
ADI                                0.527875   
ADM                                0.260184   
ADP                                0.739091   
AEE                                0.213845   
AEP                               -0.995334   
AIZ                                0.852022   
AJG                                0.210820   
AMGN                               1.030657   
AOS                                1.535688   
APD                                0.582536   
ARE                                0.255625   
ATO                                0.464697   
AVY                                0.618686   
AWK                                0.609630   
BAX                               -0.443457   
BDX                                0.535858   
BEN                                0.001657   
BLK                                0.670461   
BR                                 1.059901   
BX                                -0.382037   
CAG                               -2.353265   
CBOE                               0.775709   
CL                                 0.170226   
CLX                                0.429321   
CMCSA                              0.867682   
CMI                                0.510039   
CMS                                0.410581   
CPB                                0.120600   
CSCO                               0.788641   
CSX                                0.496798   
EMN                                0.652065   
ES                                 0.382140   
ETR

In [5]:
data2 =high_div(group2)

In [8]:
data2

mktCap   price    volAvg  lastDiv  dividend_yield  \
symbol                                                            
FMC      13706068992  106.35    791493   1.8800        0.017677   
GLW      35092934656   41.22   4366084   0.9200        0.022319   
GPC      18649890816  129.09    722542   3.2100        0.024866   
GRMN     29615308800  154.13    601546   2.5000        0.016220   
GWW      23900819456  458.66    227234   6.2100        0.013539   
HD      353895481344  332.84   3748234   6.3000        0.018928   
HON     159275597824  229.32   3117804   3.6900        0.016091   
HRL      25661831168   47.34   2023382   0.9675        0.020437   
HSY      37106102272  179.26    909519   3.2160        0.017940   
INTC    215020994560   53.00  24631765   1.7025        0.032123   
ITW      71512752128  226.39    916423   4.5600        0.020142   
JCI      50829426688   70.92   4468976   1.0600        0.014946   
JNJ     452391763968  171.79   6691709   4.0900        0.023808   
KMB      45776027648  135.66   2462846   4.4200        0.032581   
KR       29807323136   39.89   7953322   0.7200        0.018050   
LHX      46582611968  227.25   1081725   3.7400        0.016458   
LIN     155390164992  298.81   2007068   4.0460        0.013540   
LLY     234145955840  244.15   3428682   3.1800        0.013025   
LMT     105828933632  380.77   1149755  10.2000        0.026788   
LNC      11475683328   60.28   1326471   2.0600        0.034174   
LNT      14660413440   58.61   1363461   1.9685        0.033586   
MCD     181290450944  242.96   2440426   5.1200        0.021073   
MDLZ     91151630336   64.89   6556474   1.2600        0.019417   
MMC      74962706432  147.41   1906496   1.9300        0.013093   
NEM      48035467264   60.11   6748084   1.7500        0.029113   
NSC      66393939968  265.32   1229469   3.8600        0.014548   

        fiveYDividendperShareGrowthPerShare  \
symbol                                        
FMC                                1.722041   
GLW                                0.851758   
GPC                                0.293500   
GRMN                               0.195537   
GWW                                0.355839   
HD                                 1.530625   
HON                                0.682067   
HRL                                0.953839   
HSY                                0.414704   
INTC                               0.428825   
ITW                                1.160312   
JCI                                0.323956   
JNJ                                0.350118   
KMB                                0.219428   
KR                                 0.733318   
LHX                                0.680481   
LIN                                0.355115   
LLY                                0.459487   
LMT                                0.587158   
LNC                                0.923522   
LNT                                0.385541   
MCD                                0.415998   
MDLZ                               0.884854   
MMC                                0.565808   
NEM                                9.231577   
NSC                                0.596564   

        threeYDividendperShareGrowthPerShare  dividendYielPercentageTTM  \
symbol                                                                    
FMC                                 1.660358                   1.767748   
GLW                                 0.418052                   2.231926   
GPC                                 0.168611                   2.486637   
GRMN                                0.156973                   1.622007   
GWW                                 0.208035                   1.353944   
HD                                  0.688442                   1.892801   
HON                                 0.339004                   1.609105   
HRL                                 0.411464                   2.043726   
HSY                                 0.239925                   1.79404

In [6]:
data3 =high_div(group3)

In [9]:
data3

mktCap   price   volAvg  lastDiv  dividend_yield  \
symbol                                                           
OMC      15501699072   72.30  1690669   2.7000        0.037344   
PEG      30945486848   61.22  1996793   2.0000        0.032669   
PEP     217240027136  157.18  4946015   4.1440        0.026365   
PG      342238035968  139.79  8497993   3.3215        0.023761   
PKG      12694061056  133.63   554415   3.7900        0.028362   
PPG      38670200832  162.92  1129050   2.1600        0.013258   
PRU      39203000320   99.50  1906849   4.5000        0.045226   
QCOM    163424649216  144.88  8103931   2.6300        0.018153   
RHI      10473971712   92.87   828180   1.4400        0.015506   
ROK      34736041984  299.25   718706   4.2300        0.014135   
RSG      37065252864  116.18  1119822   1.7000        0.014632   
SJM      14141241344  130.50   843560   3.6000        0.027586   
SNA      12121234432  224.59   419742   4.7700        0.021239   
SRE      39576915968  130.72  1638141   4.2900        0.032818   
STX      19403960320   85.48  3025344   2.6600        0.031118   
TXN     172501794816  186.85  4258957   4.9800        0.026652   
WBA      40247844864   46.53  5718974   1.8715        0.040221   
WEC      29660352512   94.03  1175179   2.6215        0.027879   
WM       61795172352  146.39  1310225   2.2400        0.015302   
WU        9502831616   23.22  3985149   0.9200        0.039621   
XEL      36743389184   68.27  2511336   1.7755        0.026007   
YUM      36579262464  122.79  1615452   1.9400        0.015799   

        fiveYDividendperShareGrowthPerShare  \
symbol                                        
OMC                                0.284348   
PEG                               -0.777760   
PEP                                0.451557   
PG                                 0.184654   
PKG                                0.367007   
PPG                                0.481761   
PRU                               -4.996765   
QCOM                               0.445056   
RHI                                0.696259   
ROK                                0.538747   
RSG                                0.435702   
SJM                                0.334261   
SNA                                1.035637   
SRE                                0.745764   
STX                                0.280483   
TXN                                1.605115   
WBA                                0.519693   
WEC                                0.508095   
WM                                -0.907542   
WU                                 0.455899   
XEL                                0.359705   
YUM                                0.136057   

        threeYDividendperShareGrowthPerShare  dividendYielPercentageTTM  \
symbol                                                                    
OMC                                 0.177890                   3.734440   
PEG                                -0.798451                   3.266906   
PEP                                 0.272058                   2.636468   
PG                                  0.120100                   2.376064   
PKG                                 0.243077                   2.836189   
PPG                                 0.233920                   1.687945   
PRU                                -4.289870                   4.522613   
QCOM                                0.163413                   1.815295   
RHI                                 0.420914                   1.550555   
ROK                                 0.337189                   1.413534   
RSG                                 0.253454                   1.463247   
SJM                                 0.146975                   2.758621   
SNA                                 0.510443                   2.123870   
SRE                                 0.471779                   3.281824   
STX                                 0.369059                   3.111839   
TXN                      